In [1]:
# Home assignment from Wirecard.
# received 16.01 
# Notebook for prototyping

In [2]:
#Import packages
import pandas as pd
import numpy as np
import scipy as sp
from scipy.special import gamma
from scipy.special import gammaln as lnG
from scipy import optimize


import datetime as dt

# Task 1

In [3]:
#load the data
df = pd.read_csv("all_transactions.csv",names=['ID','date'])
print(df.shape)
df.head()

(6919, 2)


ID      date
0   1  19970101
1   1  19970118
2   1  19970802
3   1  19971212
4   2  19970101

## Prepare the dataset

In [4]:
# Remove duplications
df_unique = df.drop_duplicates()
print('Number of unique samples: {}'.format(len(df_unique)))
print('Number of unique customers: {}'.format(len(df_unique.ID.drop_duplicates())))

Number of unique samples: 6696
Number of unique customers: 2357


In [5]:
# train-validation split
split_date_b = 19970101 # Jan 1997
split_date_e = 19971001 # Oct 1997
#query = 'date >= {} and date < {}'.format(split_date_b,split_date_e)
#query = (df_unique.date >= split_date_b) & df_unique.date < split_date_e
df_train = df_unique[(df_unique.date >= split_date_b) & (df_unique.date < split_date_e)] # training part
#df_train = df_unique.query(query) # training part
df_val = df_unique[df_unique.date >= split_date_e] # rest is our validation part
print('Training   data size: {}'.format(df_train.shape))
print('Validation data size: {}'.format(df_val.shape))

Training   data size: (4814, 2)
Validation data size: (1882, 2)


In [6]:
# save the .csv file
df_train.reset_index(drop=True).to_csv('cal_period_transactions.csv')

# Task 2

In [7]:
# read the .csv file 
df = pd.read_csv("cal_period_transactions.csv",index_col='Unnamed: 0')
df.shape

(4814, 2)

## Parameters calculation 

### Convert to a proper datetime format

In [8]:
df['datetime'] = pd.to_datetime(df['date'],format='%Y%m%d')

### x: number of transactions done by customer

In [9]:
df['x'] = df.groupby('ID')['ID'].transform(lambda s: s.count() - 1)
df.head()

ID      date   datetime  x
0   1  19970101 1997-01-01  2
1   1  19970118 1997-01-18  2
2   1  19970802 1997-08-02  2
3   2  19970101 1997-01-01  1
4   2  19970113 1997-01-13  1

### tx: duration in weeks between customer's last and first transaction

In [10]:
# create temp df with first and last date columns
df_temp = df.datetime.groupby(df['ID']).agg(['first','last'])

In [11]:
# find the difference between the transactions 
df_temp['tx_days'] = (df_temp['last'] - df_temp['first'])
# convert it to weeks
df_temp['tx'] = df_temp['tx_days']/np.timedelta64(1,'W')
# round to 2 decimals as in the example
df_temp['tx'] = df_temp['tx'].round(2)

In [12]:
df_temp.head()

first       last  tx_days     tx
ID                                      
1  1997-01-01 1997-08-02 213 days  30.43
2  1997-01-01 1997-01-13  12 days   1.71
3  1997-01-01 1997-01-01   0 days   0.00
4  1997-01-01 1997-01-01   0 days   0.00
5  1997-01-01 1997-01-01   0 days   0.00

### T: Duration in weeks between end of calibration period and the first customer's transaction 

In [13]:
df_temp['T_days'] = dt.datetime.strptime(str(split_date_e), '%Y%m%d') - df_temp['first'] - np.timedelta64(1,'D')# -1 to take the last day into account

In [14]:
df_temp['T'] = (df_temp['T_days'] / np.timedelta64(1,'W')).round(2)

In [15]:
df_temp.head(5)

first       last  tx_days     tx   T_days      T
ID                                                      
1  1997-01-01 1997-08-02 213 days  30.43 272 days  38.86
2  1997-01-01 1997-01-13  12 days   1.71 272 days  38.86
3  1997-01-01 1997-01-01   0 days   0.00 272 days  38.86
4  1997-01-01 1997-01-01   0 days   0.00 272 days  38.86
5  1997-01-01 1997-01-01   0 days   0.00 272 days  38.86

### Merge into the initial DF

In [16]:
df = pd.merge(df,df_temp.drop(columns=['first','last','tx_days','T_days']),on=['ID'])

In [17]:
df.head()

ID      date   datetime  x     tx      T
0   1  19970101 1997-01-01  2  30.43  38.86
1   1  19970118 1997-01-18  2  30.43  38.86
2   1  19970802 1997-08-02  2  30.43  38.86
3   2  19970101 1997-01-01  1   1.71  38.86
4   2  19970113 1997-01-13  1   1.71  38.86

### Prepare the output df

In [18]:
# only unique customers should be stored
df_out = df.drop_duplicates(subset=['ID'])

In [19]:
df_out.head()

ID      date   datetime  x     tx      T
0   1  19970101 1997-01-01  2  30.43  38.86
3   2  19970101 1997-01-01  1   1.71  38.86
5   3  19970101 1997-01-01  0   0.00  38.86
6   4  19970101 1997-01-01  0   0.00  38.86
7   5  19970101 1997-01-01  0   0.00  38.86

In [20]:
# prepare the output df
df_out = df_out.reset_index().drop(columns=['date','datetime','index'])
# rename ID column
df_out.rename(columns={'ID': 'Customer ID'},inplace=True)
# Save into .csv file
df_out.to_csv('summary_customers.csv')

In [21]:
df_out.head()

Customer ID  x     tx      T
0            1  2  30.43  38.86
1            2  1   1.71  38.86
2            3  0   0.00  38.86
3            4  0   0.00  38.86
4            5  0   0.00  38.86

In [22]:
# clean the memory
del df_temp

To be omplemented
* check whether dates are in chronological order, i.e. avoid negative values 

In [23]:
df_test = pd.read_csv('summary_customers.csv')

# Task 3

The aim of this assignment is to fit a model to the data, so that predictions about the customers’ purchase behavior in future can be made. The model is defined by four parameters namely r, α, a, b and they are always greater than 0. For fitting the model (i.e. finding the parameters r, α, a, b), Maximum Likelihood Estimation (MLE) can be used.

In [24]:
# load the .csv file
df = pd.read_csv('summary_customers.csv',index_col='Unnamed: 0')
df.head()

Customer ID  x     tx      T
0            1  2  30.43  38.86
1            2  1   1.71  38.86
2            3  0   0.00  38.86
3            4  0   0.00  38.86
4            5  0   0.00  38.86

In [48]:
# Implementing in the form of class
class CustomFunction:
    def __init__(self, verbose=False):
        self.verbose = verbose
        
        #initialize model parameters
        self.__initialize_par()
        
    def __obj_f(self, params, df):
        #update parameters
        self.__update_params(params)
        #normalise alpha
        self.alpha*=self.norm
        # protection from negative parameters
        if self.r <=0 or self.b <=0 or self.alpha <= 0 or self.a <= 0:
            return np.inf
        N = len(df)
        obj_i = self.__loss(df)
        out = obj_i.sum() * (-1) / N
        print(' NLL: ',out,' Pars: r = ',self.r,' alpha = ',self.alpha,' a = ',self.a,' b = ',self.b)
        if df.isin([np.inf]).values.any():
            return np.inf
        return out
    
    def __loss(self, df):
        lnA1 = lnG(self.r+df.x) + self.r*np.log(self.alpha) - lnG(self.r)
        lnA2 = lnG(self.a+self.b) + lnG(self.b+df.x) - lnG(self.b) - lnG(self.a+self.b+df.x)
        lnA3 = -(self.r+df.x)*np.log(self.alpha+df['T'])
        lnA4 = np.log(self.alpha) - np.log(self.b+df.x-1) - (self.r+df.x)*np.log(self.alpha + df.tx)
        deltaA4 = self.__deltaA4(df.x,np.exp(lnA4))
        out = lnA1 + lnA2 + np.log(np.exp(lnA3) + deltaA4)
        return out
    
    def __deltaA4(self,x,A4):
        """function to change NaN -> 0 at A4"""
        A4[x <= 0] = 0
        return A4
    
    def __update_params(self, new_params):
        """ Update model parameters."""
        self.r = new_params[0].copy()
        self.alpha = new_params[1].copy()
        self.a = new_params[2].copy()
        self.b = new_params[3].copy()
    
    def __initialize_par(self):
        # initialise with Gaus(1,0.05)
        self.r, self.alpha, self.a, self.b = np.random.normal(1, 0.05,4)
    
    def set_r(r):
        if r <= 0: 
            raise ValueError('r should be positive')
        self.r = r
        
    def set_alpha(alpha):
        if alpha <= 0: 
            raise ValueError('alpha should be positive')
        self.alpha = alpha
    
    def set_a(a):
        if a <= 0: 
            raise ValueError('a should be positive')
        self.a = a
        
    def set_b(b):
        if b <= 0: 
            raise ValueError('b should be positive')
        self.b = b
    
    def set_parameters(r, alpha, a, b):
        self.set_r(r), self.set_alpha(alpha), self.set_a(a), self.set_b(b)
    
    def fit(self, df, minimizer_strategy = [(2,'Nelder-Mead')]):
        """Implementation of the custom minimisation procedure. """
        
        norm_df = self.__normalise_data(df)
    
        for i in range(1,self.num_iter+1):
            print('Step ',i)
            for minimizer in minimizer_strategy:
                print('Run ',minimizer)
                initial_pars = [self.r,self.alpha,self.a,self.b]
                if self.verbose:
                    print('Initialisation: r = ',self.r, ' alpha = ',self.alpha, ' a = ',self.a, ' b = ',self.b)
                self.res = sp.optimize.minimize(self.__obj_f,x0 = initial_pars,args=(norm_df), method=minimizer) 
                if i!= self.num_iter+1 and self.verbose:
                    self.print_final_results()
                
    def fit_global(self, df, minimizer_strategy = 'L-BFGS-B',num_iter = 15000):
        """Implementation of the global (brut-force) minima finding algorithm - basinhopping
        https://docs.scipy.org/doc/scipy/reference/generated/scipy.optimize.basinhopping.html#scipy.optimize.basinhopping
        Large number of iterations is recommended due to a step-based optimisation procedure.
        Fit succeed if 15% of num_iter the global minimum candidate remains the same.
        
        Parameters:
        df - pandas DataFrame with the input data of the next format (x,tx,T),
        minimizer_strategy - The minimization method (default: L-BFGS-B),
        num_iter - number of max iterations
        """
        
        norm_df = self.__normalise_data(df)
        
        initial_pars = [self.r,self.alpha,self.a,self.b]
        sp.optimize.minimize(self.__obj_f,x0 = initial_pars,args=(norm_df), method='Nelder-Mead') 
        initial_pars = [self.r,self.alpha,self.a,self.b]
        self.res = sp.optimize.basinhopping(self.__obj_f,x0 = initial_pars, 
                                            minimizer_kwargs={"method": minimizer_strategy,'args':(norm_df)},
                                            stepsize = 0.1,
                                            niter = num_iter,
                                            niter_success = int(num_iter*0.15),
                                            disp = self.verbose)
    
    def __normalise_data(self,df):
        """Method to normnalise parameters tx and T
        """
        df_temp = df.copy()
        self.__norm_sf(df)
        df_temp['tx']*=self.norm
        df_temp['T']*=self.norm
        return df_temp
    
    def __norm_sf(self,df):
        """function to compute the normalisation factor
        """
        max_T = df['T'].max()
        self.norm = 10./ max_T
    
    def print_final_results(self):
        """function print final results
        """
        #print('*********Fit Success: ',self.res.success,'*********')
        #print('Fit status',self.res.status)
        print('NLL: ',self.res.fun)
        print('Optimized parameters: r = ',self.r, ' alpha = ',self.alpha, ' a = ',self.a, ' b = ',self.b)
        if self.verbose:
            print(self.res.message)


## Minimizers

### Nelder-Mead

the most robust optimizer in scipy. converges even from not very good starting values
Problems: takes a large number of iterations. Can get stuck in almost local minima or stops just short of minimum. Doesn't use gradient for convergence check.


### Newton

"newton" is a simple solver implemented in statsmodels. It includes now a ridge factor to reduce problems with near singular hessian.
works well for discrete models, few iterations, uses Hessian
problems: breaks if Hessian is not positive definite. Doesn't have line search and might break if gradient is very large at the starting values.

### BFGS

works well and fast if we are close enough to the minimum. Finds an optimum with very small gradient.
problems: can diverge or fail to converge if gradient is large, or shape of function is not "nice" during the optimization.

### basinhopping

Find the global minimum of a function using the basin-hopping algorithm

Basin-hopping is a two-phase method that combines a global stepping algorithm with local minimization at each step. Designed to mimic the natural process of energy minimization of clusters of atoms, it works well for similar problems with “funnel-like, but rugged” energy landscapes [5].

As the step-taking, step acceptance, and minimization methods are all customizable, this function can also be used to implement other two-phase methods.

In [49]:
df.isin([np.nan, np.inf, -np.inf]).values.any()

False

In [ ]:
#np.random.seed(1)

model = CustomFunction(verbose=True)
#model.fit(df,minimizer_strategy=['Nelder-Mead','L-BFGS-B'])
model.fit_global(df,minimizer_strategy='Nelder-Mead')
model.print_final_results()

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:29: RuntimeWarning: invalid value encountered in log


 NLL:  4.68696925641297  Pars: r =  0.9403004889312438  alpha =  0.24956266103492872  a =  0.9795906515924636  b =  0.9411573901190685
 NLL:  4.810687167521556  Pars: r =  0.9873155133778061  alpha =  0.24956266103492872  a =  0.9795906515924636  b =  0.9411573901190685
 NLL:  4.637314268412062  Pars: r =  0.9403004889312438  alpha =  0.2620407940866752  a =  0.9795906515924636  b =  0.9411573901190685
 NLL:  4.704301243463783  Pars: r =  0.9403004889312438  alpha =  0.24956266103492872  a =  1.028570184172087  b =  0.9411573901190685
 NLL:  4.682026559059837  Pars: r =  0.9403004889312438  alpha =  0.24956266103492872  a =  0.9795906515924636  b =  0.988215259625022
 NLL:  4.546419914491939  Pars: r =  0.8932854644846816  alpha =  0.25580172756080194  a =  1.0040804178822755  b =  0.9646863248720453
 NLL:  4.417864101757552  Pars: r =  0.8462704400381196  alpha =  0.25892126082373856  a =  1.0163253010271813  b =  0.9764507922485335
 NLL:  4.5075476887180015  Pars: r =  0.893285464484

 NLL:  2.5839782972496046  Pars: r =  0.16688276168767952  alpha =  0.4151171327182489  a =  0.050483067001528006  b =  2.1863611069058235
 NLL:  2.581873724416196  Pars: r =  0.15938892400771157  alpha =  0.41620364487498374  a =  0.04509885722188017  b =  2.2012884640258035
 NLL:  2.579213134205363  Pars: r =  0.16573170080030933  alpha =  0.4169912152667261  a =  0.03665522067770098  b =  2.200439106306238
 NLL:  2.6012882853073  Pars: r =  0.1142957251270374  alpha =  0.4268331204147866  a =  0.05858446949189927  b =  2.2068938379559713
 NLL:  2.576415081489189  Pars: r =  0.1774396338312571  alpha =  0.41640482152818825  a =  0.017345062150324386  b =  2.212903422794219
 NLL:  2.5663663127364447  Pars: r =  0.162419759430429  alpha =  0.4236587857657273  a =  0.003207307770707296  b =  2.226319471054677
 NLL:  2.5749986103271842  Pars: r =  0.16290402858845476  alpha =  0.41929466160591594  a =  0.026223162473623145  b =  2.210356582516794
 NLL:  2.573515003001501  Pars: r =  0.15

 NLL:  2.2366824637800073  Pars: r =  0.24639430803061543  alpha =  0.9042569459835346  a =  0.13885894190177844  b =  0.0934921343189673
 NLL:  2.4587301075989147  Pars: r =  0.25746774355734175  alpha =  0.9183601171532185  a =  0.1441324655550307  b =  0.016762109121012114
 NLL:  2.225429880031569  Pars: r =  0.24331314735103582  alpha =  0.8720333742579711  a =  0.1303650427620009  b =  0.2320191539361104
 NLL:  2.2399387093726744  Pars: r =  0.248127803802537  alpha =  0.8545825119331245  a =  0.1268024759143544  b =  0.29630498681842615
 NLL:  2.221017932660341  Pars: r =  0.24682768197359584  alpha =  0.8918383374709321  a =  0.13584482540492243  b =  0.144195347443832
 NLL:  2.2365081063929115  Pars: r =  0.24315372849268585  alpha =  0.9031933666920676  a =  0.14054613581613018  b =  0.09987359943653579
 NLL:  2.2226928273133426  Pars: r =  0.24817954428680372  alpha =  0.8765809716530456  a =  0.1316553813052645  b =  0.2059789975705208
 NLL:  2.22605443223278  Pars: r =  0.2

 NLL:  2.0019798791288963  Pars: r =  0.06682959418128223  alpha =  1.0317534072094134  a =  0.01768752460164878  b =  0.03359751169825692
 NLL:  1.9855635331346944  Pars: r =  0.06032992342677121  alpha =  1.0368095850084458  a =  0.013198193787689856  b =  0.0298963829807577
 NLL:  1.926878833330289  Pars: r =  0.04733058191774918  alpha =  1.0469219406065102  a =  0.004219532159772011  b =  0.022494125545759257
 NLL:  1.9386691166436065  Pars: r =  0.05309888220587025  alpha =  1.0459614162481015  a =  0.009465138891363443  b =  0.010659232189735648
 NLL:  1.741080490648329  Pars: r =  0.04032920173303417  alpha =  1.0552137668273358  a =  0.0017751848783534238  b =  0.004407529109561589
 NLL:  1.8132437188019006  Pars: r =  0.04571654945584265  alpha =  1.0508193539748554  a =  0.0011313615395308028  b =  0.014253334901163685
 NLL:  1.9014679169720163  Pars: r =  0.04968203991273685  alpha =  1.0476873468029544  a =  0.006354563500438715  b =  0.013279673776818794
 NLL:  1.78695221

...

 NLL:  -2.0661510916090955  Pars: r =  77.88639700637927  alpha =  894.9745461177484  a =  1.260687740923047e-07  b =  5.204340745781329e-07
 NLL:  -1.9092728507736274  Pars: r =  77.88652294814074  alpha =  894.9714416660372  a =  2.791643990761019e-07  b =  1.248144534587986e-06
 NLL:  -1.9238422637534975  Pars: r =  77.88654047364523  alpha =  894.9716217498561  a =  1.8535026676279315e-07  b =  1.3519331483728532e-06
 NLL:  -2.08944559484389  Pars: r =  77.88640708778951  alpha =  894.9746495069791  a =  8.7243056823601e-08  b =  5.267824548157104e-07
 NLL:  -1.832028651658029  Pars: r =  77.88632286935714  alpha =  894.9759833017216  a =  1.3200358416731367e-07  b =  1.0418494252271928e-08
 NLL:  -1.9657685574927544  Pars: r =  77.8864860725732  alpha =  894.9727121378224  a =  1.7201359611392327e-07  b =  1.0165544848427078e-06
 NLL:  -2.0932048472984457  Pars: r =  77.88642089346305  alpha =  894.9746272899934  a =  3.4929443401795955e-08  b =  6.406202431487681e-07
 NLL:  -2.22

 NLL:  -3.1075591460906256  Pars: r =  77.88630591109201  alpha =  894.9768594758418  a =  2.653386495793822e-10  b =  2.4908326465207007e-09
 NLL:  -3.119346431425141  Pars: r =  77.88630588064107  alpha =  894.976860075829  a =  2.518498485782901e-10  b =  2.3312362207825993e-09
 NLL:  -3.2255984131028748  Pars: r =  77.88630568876091  alpha =  894.9768642099492  a =  2.7876711716314402e-11  b =  1.5830871008501436e-09
 NLL:  -3.149217091549886  Pars: r =  77.88630581629874  alpha =  894.9768614761273  a =  1.7123212250532224e-10  b =  2.0905794072424537e-09
 NLL:  -3.289715623603232  Pars: r =  77.88630558599735  alpha =  894.9768658620126  a =  4.7783518246221364e-11  b =  1.0593719354281667e-09
 NLL:  -3.183470489817781  Pars: r =  77.88630574687184  alpha =  894.9768628566195  a =  1.1864108792702026e-10  b =  1.795525579434429e-09
 NLL:  -3.2789114613776063  Pars: r =  77.88630560801806  alpha =  894.9768656176038  a =  1.3459018770416338e-11  b =  1.205417923818379e-09
 NLL:  -

 NLL:  -4.4123547841085955  Pars: r =  77.88630521190443  alpha =  894.9768712319143  a =  4.583319704154749e-14  b =  2.70990295724386e-12
 NLL:  -4.330455055661638  Pars: r =  77.88630521085275  alpha =  894.9768712389258  a =  3.177954278689425e-13  b =  3.641855342969072e-12
 NLL:  -4.452683941777855  Pars: r =  77.88630522632842  alpha =  894.9768710967697  a =  4.2901050340636873e-13  b =  1.1318887918910031e-12
 NLL:  -4.539386304928765  Pars: r =  77.88630522481776  alpha =  894.9768711124789  a =  2.026552496105917e-13  b =  9.281876313618584e-13
 NLL:  -4.5500227362300105  Pars: r =  77.8863052325973  alpha =  894.9768710395281  a =  2.670002903742169e-13  b =  6.200741306814664e-13
 NLL:  -4.665103245855488  Pars: r =  77.88630522503715  alpha =  894.9768711116309  a =  1.427106403122856e-13  b =  3.394409956156917e-13
 NLL:  -4.468426456718713  Pars: r =  77.8863052195498  alpha =  894.9768711610081  a =  1.5308868398370662e-13  b =  1.7324004223156824e-12
 NLL:  -4.4946335

 NLL:  -0.6060265489239922  Pars: r =  80.48761616036242  alpha =  903.4176063534895  a =  3.317527399312294e-07  b =  0.0022612611268725945
 NLL:  -0.6045159064763307  Pars: r =  80.51535875586828  alpha =  901.1262444641419  a =  9.587687611902402e-06  b =  0.002262007175563476
 NLL:  -0.606549598937819  Pars: r =  80.59423544455164  alpha =  911.9626396896446  a =  4.835184145450287e-06  b =  0.0022482542650704568
 NLL:  inf  Pars: r =  80.66856890947793  alpha =  920.1070773982171  a =  3.975545837496145e-06  b =  0.002237286214732133
 NLL:  -0.6051357120440163  Pars: r =  80.52748995383224  alpha =  903.8267726257945  a =  7.047192099346901e-06  b =  0.002258895631674501
 NLL:  -0.6065598150665067  Pars: r =  80.36224998765098  alpha =  928.4705217207243  a =  6.603156407774066e-06  b =  0.002221430747951195
 NLL:  inf  Pars: r =  80.21646255052394  alpha =  947.2066271920638  a =  7.926790339833704e-06  b =  0.002192284374107756
 NLL:  inf  Pars: r =  80.40596491263314  alpha =  

 NLL:  -0.6078127165237672  Pars: r =  80.5864722582179  alpha =  916.6891851286765  a =  3.27651311911831e-08  b =  0.002242886611869009
 NLL:  inf  Pars: r =  80.5916192491402  alpha =  916.4242071071938  a =  2.7201008390017448e-08  b =  0.002243320612641664
 NLL:  -0.607813185229908  Pars: r =  80.58386327848386  alpha =  916.8486347818924  a =  3.334799594029327e-08  b =  0.002242630769581836
 NLL:  inf  Pars: r =  80.58512045598701  alpha =  916.8048574785838  a =  3.012430136377463e-08  b =  0.002242706901524294
 NLL:  -0.6078139149326435  Pars: r =  80.58613430766017  alpha =  916.7181032161534  a =  3.2104923734330986e-08  b =  0.0022428416842828302
 NLL:  -0.6078142185443407  Pars: r =  80.58775196914948  alpha =  916.6349228791788  a =  4.052811426389524e-08  b =  0.0022429746850866376
 NLL:  -0.6078179349093116  Pars: r =  80.5872915986963  alpha =  916.6687377149615  a =  2.14604367658117e-08  b =  0.0022429274154346737
 NLL:  inf  Pars: r =  80.58900575880253  alpha =  91

In [27]:
basinhopping step 8441: f 1.96268 trial_f 1.96268 accepted 1  lowest_f 0.395238
NLL:  0.39523751277941316
Optimized parameters: r =  89.93945450067707  alpha =  515.8638751544526  a =  0.014407165509005893  b =  40.98760269215206
['success condition satisfied']

SyntaxError: invalid syntax (<ipython-input-27-91599662619f>, line 1)

From global optimizet

NLL:  2.3083137820714543
Optimized parameters: r =  0.5628339908409673  alpha =  1.4942441633441137  a =  -0.3246705921018955  b =  2.065940938280864

In [ ]:
NLL:  2.320103966291929
Optimized parameters: r =  -0.042541935932822406  alpha =  0.9366411141859613  a =  -0.048999004197085916  b =  3.4013409255752576